# Computation of layer by layer containment corrections




## Setup

In [1]:
import sys
sys.path.insert(0, '..')
sys.path.insert(1, 'python/')

import ROOT
import root_numpy as rnp
import python.l1THistos as histos
import math
import uuid
import pandas as pd

from drawingTools import *

ROOT.enableJSVis()
#ROOT.enableJSVis()

#from drawingTools import *

normalized_histos = list()
    

Welcome to JupyROOT 6.14/02


In [4]:
# %load python/drawingTools.py


In [5]:
# %load samples.py
import ROOT
import pandas as pd
import python.selections as selections

version = 'v87t'
version_V8 = version
version_V9 = 'v130'
version_V10 = 'v106'


# -------------------------------------------------------------------------

samples_ele = [
    Sample('ele_flat2to100_PU0', 'PU0', version, 'ele'),
    Sample('ele_flat2to100_PU200', 'PU200', version, 'ele')
    ]

samples_ele_V8 = [
    Sample('ele_flat2to100_PU0', 'PU0', version_V8, 'V8'),
    Sample('ele_flat2to100_PU200', 'PU200', version_V8, 'V8')
    ]


samples_ele_V9 = [
    Sample('ele_flat2to100_PU0_calibs', 'PU0', version_V9, 'ele-V9'),
    Sample('ele_flat2to100_PU200_calibs', 'PU200', version_V9, 'ele-V9')
    ]

samples_ele_V10 = [
    Sample('ele_flat2to100_PU0_calibs', 'PU0', version_V10, 'ele-V10'),
    Sample('ele_flat2to100_PU200_tps', 'PU200', version_V10, 'ele-V10')
    ]

samples_photons = [
    Sample('photon_flat8to150_PU0_tps', 'PU0', version, 'photon'),
#     Sample('photon_flat8to150_PU200_tps', 'PU200', version, 'photon')
    ]

samples_photons_V8 = [
    Sample('photon_flat8to150_PU0', 'PU0', version_V8, 'photon'),
    Sample('photon_flat8to150_PU200', 'PU200', version_V8, 'photon')
    ]

samples_photons_V9 = [
    Sample('photon_flat8to150_PU0_calibs', 'PU0', version_V9, 'photons-V9'),
#     Sample('photon_flat8to150_PU200_tps', 'PU200', version_V9, 'photons-V9')
    ]

samples_pions = [
    Sample('pion_flat2to100_PU0', 'PU0', version, 'pions'),
    ]

samples_nugus = [
    Sample('nugun_alleta_pu0', 'PU0', version, 'mb'),
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

samples_nugunrates = [
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

samples_nugunrates_V8 = [
    Sample('nugun_alleta_pu200', 'PU200', version, 'V8')
    ]

samples_nugunrates_V9 = [
    Sample('nugun_alleta_pu200', 'PU200', version, 'V9')
    ]


In [6]:
# %load python/settings.py

# === samples =====================================================
import pprint
import python.plotters_config as plotters



samples = []

# samples += samples_nugunrates
# samples += samples_nugunrates_V8
samples += samples_ele_V9

for smp in samples:
    smp.open_file()
    # FIXME: hugly workaround ######################%%%%^^&&**()())))_ remove for calibs versions > 112
#     smp.oldStyle = True

sample = 'ele-V9'

# === TP ==========================================================
tps = ['HMvDR',
       'HMvDRshapeDr']


# === Load the Histo Primitives ====================================
histo_primitives = samples[0].build_file_primitive_index()


# print histo_primitives.data.unique()
# === TP selections ================================================
tp_select = {}

for tp in tps:
    tp_select[tp] = histo_primitives[histo_primitives.tp == tp].tp_sel.unique().tolist()

# ==== GEN selections ===============================================
gen_select ={}
for tp in tps:
    gen_select[tp] = histo_primitives[histo_primitives.tp == tp].gen_sel.unique().tolist()


import pprint
pp = pprint.PrettyPrinter(indent=4)
print '--- TPs: '
pp.pprint(tps)
print '--- TP selections:'
pp.pprint(tp_select)
print '--- GEN selections:'
pp.pprint(gen_select)


--- CalibrationHistos
# of plots: 60
# of primitives: 60
--- TPs: 
['HMvDR', 'HMvDRshapeDr']
--- TP selections:
{   'HMvDR': ['Em', 'all'], 'HMvDRshapeDr': ['all', 'Em']}
--- GEN selections:
{   'HMvDR': [   'GEN',
                 'GENEtaDEPt15',
                 'GENEtaDEPt10to25',
                 'GENEtaDE',
                 'GENEtaBCD',
                 'GENEtaDEPt35',
                 'GENEtaDEPt30',
                 'GENEtaDEPt40',
                 'GENEtaD',
                 'GENEtaBC'],
    'HMvDRshapeDr': [   'GENEtaDEPt35',
                        'GENEtaBCD',
                        'GENEtaDEPt10to25',
                        'GENEtaDEPt15',
                        'GENEtaDEPt40',
                        'GENEtaDE',
                        'GENEtaDEPt30',
                        'GENEtaBC',
                        'GEN',
                        'GENEtaD']}


In [7]:
import python.collections as collections
import python.selections as selections

labels_dict = {}

evm = collections.EventManager()
labels_dict.update(evm.get_labels())
selm = selections.SelectionManager()
labels_dict.update(selm.get_labels())



In [8]:
for tp in tps:
    print 'TP: {}'.format(tp)
    print histo_primitives[histo_primitives.tp == tp].tp_sel.unique()
    print histo_primitives[histo_primitives.tp == tp].gen_sel.unique()

TP: HMvDR
['Em' 'all']
['GEN' 'GENEtaDEPt15' 'GENEtaDEPt10to25' 'GENEtaDE' 'GENEtaBCD'
 'GENEtaDEPt35' 'GENEtaDEPt30' 'GENEtaDEPt40' 'GENEtaD' 'GENEtaBC']
TP: HMvDRshapeDr
['all' 'Em']
['GENEtaDEPt35' 'GENEtaBCD' 'GENEtaDEPt10to25' 'GENEtaDEPt15'
 'GENEtaDEPt40' 'GENEtaDE' 'GENEtaDEPt30' 'GENEtaBC' 'GEN' 'GENEtaD']


## Computation of the values

In [12]:
tps

['HMvDR', 'HMvDRshapeDr']

### read the calib trees

In [15]:
samples = []
samples += samples_photons_V9
samples += samples_ele_V9
# samples += samples_ele_V10
for smp in samples:
    smp.open_file()

import array
import numpy as np 

tree_data = pd.DataFrame()

for smp in samples:
    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaD', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)
                tree_name = 'CalibrationHistos/{}_{}_{}_calib'.format(tp, tp_sel, gen_sel)
                if smp.type == 'ele-V9' and tp == "HMvDRCalib":
                    tree_name = 'CalibrationHistos/{}_{}_{}_calib'.format('HMvDR', tp_sel, gen_sel)
                # get the tree
                tree = smp.histo_file.Get(tree_name)
                
                # read the branches
                df = pd.DataFrame()

                cluster_pt = np.array([list(aset)[0] for aset in rnp.tree2array(tree, branches=['pt'], cache_size=400000000)])
                cluster_eta = np.array([list(aset)[0] for aset in rnp.tree2array(tree, branches=['eta'], cache_size=400000000)])
                branches = ['e1', 'e3','e5','e7','e9','e11','e13','e15','e17','e19','e21','e23','e25','e27']

                cluster_layer_energies = np.array([np.array(list(aset)) for aset in rnp.tree2array(tree, branches=branches, cache_size=400000000)])
                gen_energy = np.array(rnp.tree2array(tree, branches='Egen', cache_size=400000000))
                
                # fill the array

                df['cl_pt'] = cluster_pt
                df['cl_layer_energies'] = cluster_layer_energies.tolist()
                df['cl_eta'] = cluster_eta
                df['cl_abseta'] = np.abs(df.cl_eta)
                df['gen_energy'] = gen_energy
                # FIXME: approx
                df['gen_pt'] = df.gen_energy/np.cosh(df.cl_eta)
        
                
                df['uncalib_energy'] = df.cl_layer_energies.apply(np.sum)
                df['uncalib_energy_nl0'] = df.cl_layer_energies.apply(lambda x: np.dot(x, [0]+[1.]*13))
                df['uncalib_pt_nl0'] = df.uncalib_energy_nl0/np.cosh(df.cl_eta)

                df.loc[:, 'smp'] = smp.type
                df.loc[:, 'pu'] = smp.label
                df.loc[:, 'tp'] = tp
                df.loc[:, 'gen_sel'] = gen_sel
                df.loc[:, 'tp_sel'] = tp_sel

                tree_data = tree_data.append(df, ignore_index=True)



------ SAMPLE: photons-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD

------ SAMPLE: ele-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD

------ SAMPLE: ele-V9, PU: PU200
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD


In [16]:
tree_data.iloc[:10]

cl_pt                                  cl_layer_energies    cl_eta  \
0   17.366413  [0.0, 3.36193776131, 8.91100978851, 11.7480335...  1.872592   
1   10.426340  [0.0, 0.77487039566, 3.49941492081, 4.89917945... -2.141374   
2   40.994465  [0.0, 0.0, 0.118730135262, 4.19929742813, 15.0... -1.666960   
3   44.075939  [0.0, 2.93075966835, 11.7980270386, 20.9090003...  1.706340   
4   70.830299  [0.0, 0.0, 5.40534543991, 26.2893505096, 49.96... -2.111467   
5  120.486267  [0.0, 4.87418460846, 21.2589416504, 44.0738754...  1.744260   
6   57.265133  [0.0, 0.0, 1.66222190857, 14.1101388931, 43.71...  2.349058   
7   11.865688  [0.0677006542683, 1.22479510307, 5.4365901947,... -1.995320   
8   77.390877  [0.0, 0.168721780181, 1.89968216419, 15.609887... -1.674180   
9  108.056412  [0.0, 0.0, 0.199966549873, 4.04307365417, 20.9... -1.608243   

   cl_abseta  gen_energy      gen_pt  uncalib_energy  uncalib_energy_nl0  \
0   1.872592   67.739655   20.345711       57.821583           57.821583   
1   2.141374   46.412971   10.757920       44.986229           44.986229   
2   1.666960  109.525742   39.937462      112.431175          112.431175   
3   1.706340  133.794144   47.025391      125.410279          125.410279   
4   2.111467  294.510956   70.277206      296.844118          296.844118   
5   1.744260  356.694122  120.986252      355.246858          355.246858   
6   2.349058  308.048096   58.280849      302.699309          302.699309   
7   1.995320   46.951447   12.536216       44.441528           44.373828   
8   1.674180  219.918640   79.653496      213.239425          213.239425   
9   1.608243  278.339264  107.171684      279.662628          279.662628   

   uncalib_pt_nl0         smp   pu     tp   gen_sel tp_sel  
0       17.366802  photons-V9  PU0  HMvDR  GENEtaBC     Em  
1       10.427220  photons-V9  PU0  HMvDR  GENEtaBC     Em  
2       40.996900  photons-V9  PU0  HMvDR  GENEtaBC     Em  
3       44.078666  photons-V9  PU0  HMvDR  GENEtaBC     Em  
4       70.833952  photons-V9  PU0  HMvDR  GENEtaBC     Em  
5      120.495359  photons-V9  PU0  HMvDR  GENEtaBC     Em  
6       57.268890  photons-V9  PU0  HMvDR  GENEtaBC     Em  
7       11.847982  photons-V9  PU0  HMvDR  GENEtaBC     Em  
8       77.234315  photons-V9  PU0  HMvDR  GENEtaBC     Em  
9      107.681233  photons-V9  PU0  HMvDR  GENEtaBC     Em

### compute the layer-by-layer corrections

In [17]:
# compute the layer calibrations on photons

calib_df = pd.DataFrame()
from sklearn.linear_model import LinearRegression
from scipy.optimize import least_squares
from scipy.optimize import lsq_linear

for smp in samples_photons_V9:
    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaD', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)

                sel_df = tree_data[(tree_data.smp == smp.type) &
                                   (tree_data.pu == smp.label) &
                                   (tree_data.tp == tp) &
                                   (tree_data.tp_sel == tp_sel) &
                                   (tree_data.gen_sel == gen_sel)]
                
                
#                 res = least_squares(fun=compute_residual, 
#                                     x0=np.array([1.]*14), 
#                                     args=(layer_energy_list, target_energy),
#                                     bounds=(np.array([0.5]*14), np.array([2.]*14)))
#                 print '   - least. sq bound: {}'.format([float("{0:0.2f}".format(i)) for i in res.x ])
#                 print sel_df.cl_layer_energies.tolist()
                lsqbregr=lsq_linear(np.array(sel_df.cl_layer_energies.tolist()), 
                                    sel_df.gen_energy.to_numpy(), 
                                    bounds = (np.array([0.5]*14), np.array([2.]*14)), 
                                    method='bvls', lsmr_tol='auto', verbose=1)
                weights = lsqbregr.x
                print '   - linear. lsq bound: {}'.format([float("{0:0.2f}".format(i)) for i in lsqbregr.x ])

                df = pd.DataFrame()
                df['layer_calib'] = [lsqbregr.x]
                df.loc[:, 'smp'] = smp.type
                df.loc[:, 'pu'] = smp.label
                df.loc[:, 'tp'] = tp
                df.loc[:, 'gen_sel'] = gen_sel
                df.loc[:, 'tp_sel'] = tp_sel

                calib_df = calib_df.append(df, ignore_index=True)

                


------ SAMPLE: photons-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
The relative change of the cost function is less than `tol`.
Number of iterations 5, initial cost 1.3149e+06, final cost 1.3103e+06, first-order optimality 6.22e-07.
   - linear. lsq bound: [2.0, 2.0, 0.77, 1.0, 1.19, 0.93, 1.02, 0.54, 1.51, 1.08, 0.8, 0.73, 1.36, 2.0]
TP: HMvDR sel: Em, gen_sel: GENEtaD
The relative change of the cost function is less than `tol`.
Number of iterations 5, initial cost 2.1376e+07, final cost 2.1346e+07, first-order optimality 8.63e-08.
   - linear. lsq bound: [0.5, 1.04, 2.0, 0.83, 0.74, 1.24, 0.63, 0.85, 1.54, 0.98, 1.23, 1.86, 0.5, 1.95]
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
The relative change of the cost function is less than `tol`.
Number of iterations 4, initial cost 2.3094e+07, final cost 2.3087e+07, first-order optimality 1.45e-06.
   - linear. lsq bound: [2.0, 2.0, 1.04, 1.01, 1.02, 1.02, 0.84, 0.66, 1.48, 1.04, 1.11, 1.74, 1.08, 0.8]
TP: HMvDRshapeDr sel: Em, gen_sel: GENE

In [18]:
calib_df.iloc[:10]

layer_calib         smp   pu  \
0  [2.0, 2.0, 0.769153414259, 1.00203925618, 1.18...  photons-V9  PU0   
1  [0.5, 1.04395886337, 2.0, 0.82623326275, 0.735...  photons-V9  PU0   
2  [2.0, 2.0, 1.03957954893, 1.00548137487, 1.019...  photons-V9  PU0   
3  [2.0, 2.0, 0.740104120439, 1.08704221771, 1.17...  photons-V9  PU0   
4  [2.0, 0.831595599723, 2.0, 0.973432139785, 0.5...  photons-V9  PU0   
5  [2.0, 2.0, 1.01817677189, 1.1212799207, 0.9261...  photons-V9  PU0   

             tp    gen_sel tp_sel  
0         HMvDR   GENEtaBC     Em  
1         HMvDR    GENEtaD     Em  
2         HMvDR  GENEtaBCD     Em  
3  HMvDRshapeDr   GENEtaBC     Em  
4  HMvDRshapeDr    GENEtaD     Em  
5  HMvDRshapeDr  GENEtaBCD     Em

### Apply layer-by-layer corrections

In [19]:
# apply layer by layer
calib_eta = 'GENEtaBC'
calib_sample = 'photons-V9'
calib_pu = 'PU0'

for smp in samples:
    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaD', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)

                sel_df = tree_data[(tree_data.smp == smp.type) &
                                   (tree_data.pu == smp.label) &
                                   (tree_data.tp == tp) &
                                   (tree_data.tp_sel == tp_sel) &
                                   (tree_data.gen_sel == gen_sel)]
                
                calib = calib_df[(calib_df.smp == calib_sample) &
                                 (calib_df.pu == calib_pu) &
                                   (calib_df.tp == tp) &
                                   (calib_df.tp_sel == tp_sel) &
                                   (calib_df.gen_sel == calib_eta)]
                calib_values = calib.layer_calib.values[0]
                # we set to 0 layer 0
                calib_values[0] = 0
#                 print calib_values
                tree_data.loc[sel_df.index, 'lcalib_energy'] = sel_df.cl_layer_energies.apply(lambda x: np.dot(x, calib_values))
                tree_data.loc[sel_df.index, 'lcalib_pt'] = tree_data.loc[sel_df.index, 'lcalib_energy']/np.cosh(sel_df.cl_eta)


------ SAMPLE: photons-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD

------ SAMPLE: ele-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD

------ SAMPLE: ele-V9, PU: PU200
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD


In [20]:
tree_data[tree_data.smp == 'ele-V9'].iloc[:10]

cl_pt                                  cl_layer_energies    cl_eta  \
72102   3.815544  [0.0, 0.0, 1.69971561432, 3.41192913055, 3.793... -2.256618   
72103  26.929020  [0.0551634952426, 1.59973239899, 11.485578537,...  1.895194   
72104  23.877455  [0.130386441946, 3.13072657585, 5.25537014008,... -1.895183   
72105  31.520269  [0.0, 6.69887924194, 16.2972736359, 28.6077136...  2.201360   
72106  31.666878  [0.240713432431, 5.29911327362, 13.972661972, ... -2.209442   
72107  91.343330  [0.0852526724339, 9.92333984375, 38.0186386108... -2.385932   
72108  88.012207  [0.0, 2.34960699081, 14.6975402832, 44.6300354...  2.386415   
72109  71.188301  [0.260772883892, 12.2854452133, 33.5756378174,... -1.886316   
72110  79.160065  [0.190564796329, 10.1607999802, 32.2133636475,...  1.875818   
72111  13.637289  [0.0952823981643, 0.387435168028, 3.2931990623...  1.916251   

       cl_abseta  gen_energy     gen_pt  uncalib_energy  uncalib_energy_nl0  \
72102   2.256618   31.082659   6.438372       18.421919           18.421919   
72103   1.895194   91.581436  26.919367       91.614853           91.559690   
72104   1.895183   91.581436  26.919662       80.579437           80.449051   
72105   2.201360  148.637558  32.496365      144.169586          144.169586   
72106   2.209442  148.637558  32.241051      146.010070          145.769357   
72107   2.385932  486.873138  88.835770      500.714113          500.628860   
72108   2.386415  486.873138  88.793625      482.663114          482.663114   
72109   1.886316  265.762390  78.783401      239.508285          239.247512   
72110   1.875818  265.762390  79.576866      264.396424          264.205859   
72111   1.916251   70.597046  20.337376       47.331139           47.235856   

       uncalib_pt_nl0     smp   pu     tp   gen_sel tp_sel  lcalib_energy  \
72102        3.815863  ele-V9  PU0  HMvDR  GENEtaBC     Em      17.553007   
72103       26.912974  ele-V9  PU0  HMvDR  GENEtaBC     Em      91.578266   
72104       23.647383  ele-V9  PU0  HMvDR  GENEtaBC     Em      81.862801   
72105       31.519539  ele-V9  PU0  HMvDR  GENEtaBC     Em     149.985639   
72106       31.618906  ele-V9  PU0  HMvDR  GENEtaBC     Em     149.631324   
72107       91.345664  ele-V9  PU0  HMvDR  GENEtaBC     Em     504.171249   
72108       88.025823  ele-V9  PU0  HMvDR  GENEtaBC     Em     481.509384   
72109       70.923248  ele-V9  PU0  HMvDR  GENEtaBC     Em     247.608688   
72110       79.110798  ele-V9  PU0  HMvDR  GENEtaBC     Em     270.886594   
72111       13.607557  ele-V9  PU0  HMvDR  GENEtaBC     Em      47.224851   

       lcalib_pt  
72102   3.635879  
72103  26.918435  
72104  24.062944  
72105  32.791092  
72106  32.456607  
72107  91.992015  
72108  87.815411  
72109  73.401860  
72110  81.111201  
72111  13.604387

### compute eta scale correction @ PU200

In [21]:
# compute the layer calibrations on photons

eta_calib_df = pd.DataFrame()
from sklearn.linear_model import LinearRegression
from scipy.optimize import least_squares
from scipy.optimize import lsq_linear

for smp in samples:
    if smp.label != 'PU200':
        continue

    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    calib_table = calib_table_by_sample[smp.type]
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)

                sel_df = tree_data[(tree_data.smp == smp.type) &
                                   (tree_data.pu == smp.label) &
                                   (tree_data.tp == tp) &
                                   (tree_data.tp_sel == tp_sel) &
                                   (tree_data.gen_sel == gen_sel)]

                df = pd.DataFrame(columns=['eta_calib_0', 'eta_calib_1', 'smp', 'pu', 'tp', 'gen_sel', 'tp_sel'])

                # uncalib eta correction

                X = sel_df.cl_abseta.to_numpy().reshape(-1, 1)
                Y = sel_df.gen_energy - sel_df.uncalib_energy_nl0.to_numpy()
                corr_eta = LinearRegression(fit_intercept=True).fit(X, Y)
                print corr_eta.coef_[0], corr_eta.intercept_
    
                df.loc[0, 'eta_calib_0'] = (corr_eta.coef_[0], corr_eta.intercept_)

#                 Y = sel_df.gen_energ


------ SAMPLE: ele-V9, PU: PU200
TP: HMvDR sel: Em, gen_sel: GENEtaBC
-41.253 80.1801
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
-30.3036 58.8577
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
-28.6653 63.2293
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD
-16.2859 39.333


In [24]:
# compute the layer calibrations on photons

eta_calib_df = pd.DataFrame()
from sklearn.linear_model import LinearRegression
from scipy.optimize import least_squares
from scipy.optimize import lsq_linear

for smp in samples:
    if smp.label != 'PU200':
        continue

    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)

                sel_df = tree_data[(tree_data.smp == smp.type) &
                                   (tree_data.pu == smp.label) &
                                   (tree_data.tp == tp) &
                                   (tree_data.tp_sel == tp_sel) &
                                   (tree_data.gen_sel == gen_sel)]

                df = pd.DataFrame(columns=['eta_calib_0', 'eta_calib_1', 'smp', 'pu', 'tp', 'gen_sel', 'tp_sel'])

                # uncalib eta correction

                X = sel_df.cl_abseta.to_numpy().reshape(-1, 1)
                Y = sel_df.gen_energy - sel_df.uncalib_energy_nl0.to_numpy()
                corr_eta = LinearRegression(fit_intercept=True).fit(X, Y)
                print corr_eta.coef_[0], corr_eta.intercept_
    
                df.loc[0, 'eta_calib_0'] = (corr_eta.coef_[0], corr_eta.intercept_)

                if True:
                    Y = sel_df.gen_energy - sel_df.lcalib_energy.to_numpy()
                    corr_eta = LinearRegression(fit_intercept=True).fit(X, Y)
                    print corr_eta.coef_[0], corr_eta.intercept_

                    df.loc[0, 'eta_calib_1'] = (corr_eta.coef_[0], corr_eta.intercept_)

                    Y = sel_df.gen_pt - sel_df.lcalib_energy.to_numpy()/np.cosh(sel_df.cl_eta)
                    corr_eta = LinearRegression(fit_intercept=True).fit(X, Y)
                    print corr_eta.coef_[0], corr_eta.intercept_
                else:
                    df.loc[0, 'eta_calib_1'] = (0, 0)

                df.loc[:, 'smp'] = smp.type
                df.loc[:, 'pu'] = smp.label
                df.loc[:, 'tp'] = tp
                df.loc[:, 'gen_sel'] = gen_sel
                df.loc[:, 'tp_sel'] = tp_sel

                eta_calib_df = eta_calib_df.append(df, ignore_index=True)

                


------ SAMPLE: ele-V9, PU: PU200
TP: HMvDR sel: Em, gen_sel: GENEtaBC
-41.253 80.1801
-44.4736 81.5294
-11.6691 22.0439
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
-30.3036 58.8577
-34.6382 62.2491
-6.94948 13.0791
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
-28.6653 63.2293
-34.4318 66.7224
-10.2039 20.3874
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD
-16.2859 39.333
-24.3133 47.031
-5.94433 12.3061


In [25]:
eta_calib_df

eta_calib_0          eta_calib_1     smp     pu            tp  \
0   (-41.253, 80.1801)  (-44.4736, 81.5294)  ele-V9  PU200         HMvDR   
1  (-30.3036, 58.8577)  (-34.6382, 62.2491)  ele-V9  PU200         HMvDR   
2  (-28.6653, 63.2293)  (-34.4318, 66.7224)  ele-V9  PU200  HMvDRshapeDr   
3   (-16.2859, 39.333)   (-24.3133, 47.031)  ele-V9  PU200  HMvDRshapeDr   

     gen_sel tp_sel  
0   GENEtaBC     Em  
1  GENEtaBCD     Em  
2   GENEtaBC     Em  
3  GENEtaBCD     Em

In [26]:
# apply eta dependent corrections
eta_calib_eta = 'GENEtaBC'
eta_calib_sample = 'ele-V9'
eta_calib_pu = 'PU200'

for smp in samples_ele_V9:
    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    calib_table = calib_table_by_sample[smp.type]
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaD', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)

                sel_df = tree_data[(tree_data.smp == smp.type) &
                                   (tree_data.pu == smp.label) &
                                   (tree_data.tp == tp) &
                                   (tree_data.tp_sel == tp_sel) &
                                   (tree_data.gen_sel == gen_sel)]
                
                calib = eta_calib_df[(eta_calib_df.smp == eta_calib_sample) &
                                 (eta_calib_df.pu == eta_calib_pu) &
                                   (eta_calib_df.tp == tp) &
                                   (eta_calib_df.tp_sel == tp_sel) &
                                   (eta_calib_df.gen_sel == eta_calib_eta)]
                calib_values = calib.eta_calib_0.values[0]
                print calib_values
                tree_data.loc[sel_df.index, 'eta_uncalib_energy_nl0'] = sel_df.uncalib_energy_nl0+calib_values[1]+sel_df.cl_abseta*calib_values[0]
                tree_data.loc[sel_df.index, 'eta_uncalib_pt_nl0'] = tree_data.loc[sel_df.index, 'eta_uncalib_energy_nl0']/np.cosh(sel_df.cl_eta)
                calib_values = calib.eta_calib_1.values[0]
                print calib_values
                tree_data.loc[sel_df.index, 'eta_lcalib_energy'] = sel_df.lcalib_energy+calib_values[1]+sel_df.cl_abseta*calib_values[0]
                tree_data.loc[sel_df.index, 'eta_lcalib_pt'] = tree_data.loc[sel_df.index, 'eta_lcalib_energy']/np.cosh(sel_df.cl_eta)

                # we set to 0 layer 0
                # calib_values[0] = 0
#                 print calib_values
                # tree_data.loc[sel_df.index, 'eta_lcalib_energy'] = sel_df.cl_layer_energies.apply(lambda x: np.dot(x, calib_values))
                


------ SAMPLE: ele-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
(-41.253017, 80.18013)
(-44.473629, 81.529419)
TP: HMvDR sel: Em, gen_sel: GENEtaD
(-41.253017, 80.18013)
(-44.473629, 81.529419)
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
(-41.253017, 80.18013)
(-44.473629, 81.529419)
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
(-28.665283, 63.229263)
(-34.431755, 66.722359)
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
(-28.665283, 63.229263)
(-34.431755, 66.722359)
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD
(-28.665283, 63.229263)
(-34.431755, 66.722359)

------ SAMPLE: ele-V9, PU: PU200
TP: HMvDR sel: Em, gen_sel: GENEtaBC
(-41.253017, 80.18013)
(-44.473629, 81.529419)
TP: HMvDR sel: Em, gen_sel: GENEtaD
(-41.253017, 80.18013)
(-44.473629, 81.529419)
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
(-41.253017, 80.18013)
(-44.473629, 81.529419)
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
(-28.665283, 63.229263)
(-34.431755, 66.722359)
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
(-28.665283, 63.229

In [23]:
#  1: 34.2000 2: -12.5900 eta: 2.1211 delta: 59.9530
#  1: 34.2000 2: -12.5900 eta: 2.1031 delta: 59.3363
#  1: 34.2000 2: -12.5900 eta: 2.1087 delta: 59.5279

In [27]:
tree_data[tree_data.smp == 'ele-V9'].iloc[:10]

cl_pt                                  cl_layer_energies    cl_eta  \
72102   3.815544  [0.0, 0.0, 1.69971561432, 3.41192913055, 3.793... -2.256618   
72103  26.929020  [0.0551634952426, 1.59973239899, 11.485578537,...  1.895194   
72104  23.877455  [0.130386441946, 3.13072657585, 5.25537014008,... -1.895183   
72105  31.520269  [0.0, 6.69887924194, 16.2972736359, 28.6077136...  2.201360   
72106  31.666878  [0.240713432431, 5.29911327362, 13.972661972, ... -2.209442   
72107  91.343330  [0.0852526724339, 9.92333984375, 38.0186386108... -2.385932   
72108  88.012207  [0.0, 2.34960699081, 14.6975402832, 44.6300354...  2.386415   
72109  71.188301  [0.260772883892, 12.2854452133, 33.5756378174,... -1.886316   
72110  79.160065  [0.190564796329, 10.1607999802, 32.2133636475,...  1.875818   
72111  13.637289  [0.0952823981643, 0.387435168028, 3.2931990623...  1.916251   

       cl_abseta  gen_energy     gen_pt  uncalib_energy  uncalib_energy_nl0  \
72102   2.256618   31.082659   6.438372       18.421919           18.421919   
72103   1.895194   91.581436  26.919367       91.614853           91.559690   
72104   1.895183   91.581436  26.919662       80.579437           80.449051   
72105   2.201360  148.637558  32.496365      144.169586          144.169586   
72106   2.209442  148.637558  32.241051      146.010070          145.769357   
72107   2.385932  486.873138  88.835770      500.714113          500.628860   
72108   2.386415  486.873138  88.793625      482.663114          482.663114   
72109   1.886316  265.762390  78.783401      239.508285          239.247512   
72110   1.875818  265.762390  79.576866      264.396424          264.205859   
72111   1.916251   70.597046  20.337376       47.331139           47.235856   

       uncalib_pt_nl0     smp   pu     tp   gen_sel tp_sel  lcalib_energy  \
72102        3.815863  ele-V9  PU0  HMvDR  GENEtaBC     Em      17.553007   
72103       26.912974  ele-V9  PU0  HMvDR  GENEtaBC     Em      91.578266   
72104       23.647383  ele-V9  PU0  HMvDR  GENEtaBC     Em      81.862801   
72105       31.519539  ele-V9  PU0  HMvDR  GENEtaBC     Em     149.985639   
72106       31.618906  ele-V9  PU0  HMvDR  GENEtaBC     Em     149.631324   
72107       91.345664  ele-V9  PU0  HMvDR  GENEtaBC     Em     504.171249   
72108       88.025823  ele-V9  PU0  HMvDR  GENEtaBC     Em     481.509384   
72109       70.923248  ele-V9  PU0  HMvDR  GENEtaBC     Em     247.608688   
72110       79.110798  ele-V9  PU0  HMvDR  GENEtaBC     Em     270.886594   
72111       13.607557  ele-V9  PU0  HMvDR  GENEtaBC     Em      47.224851   

       lcalib_pt  eta_uncalib_energy_nl0  eta_uncalib_pt_nl0  \
72102   3.635879                5.509733            1.141270   
72103  26.918435               93.557340           27.500162   
72104  24.062944               82.447174           24.234716   
72105  32.791092              133.536964           29.194948   
72106  32.456607              134.803338           29.240261   
72107  91.992015              482.382080           88.016323   
72108  87.815411              464.396421           84.694429   
72109  73.401860              241.611396           71.624005   
72110  81.111201              267.002818           79.948288   
72111  13.604387               48.364854           13.932795   

       eta_lcalib_energy  eta_lcalib_pt  
72102          -1.277574      -0.264633  
72103          88.821514      26.108117  
72104          79.106568      23.252771  
72105         133.612577      29.211479  
72106         132.898841      28.827156  
72107         479.589592      87.506800  
72108         456.906265      83.328410  
72109         245.246772      72.701687  
72110         268.991559      80.543774  
72111          43.531636      12.540457

### Fill histograms

In [28]:
class EnergyRes(histos.ResoHistos):
    def __init__(self,  name, root_file=None, debug=False):
        self.name = name
        
        self.h_energyResVenergy_raw = ROOT.TH2F(self.name + '_energyResVenergy_raw', '',
                                                100,0,1000, 
                                                100, -1.5, 1.5)
        self.h_energyResVenergy_lcalib = ROOT.TH2F(self.name + '_energyResVenergy_lcalib', '',
                                                   100,0,1000, 
                                                   100, -1.5, 1.5)
        self.h_energyResVenergy_etacalib = ROOT.TH2F(self.name + '_energyResVenergy_etacalib', '',
                                                     100,0,1000, 
                                                     100, -1.5, 1.5)

        
        self.h_ptResVpt_raw = ROOT.TH2F(self.name + '_ptResVpt_raw', '',
                                        100,0,100, 
                                        100, -1.5, 1.5)
        self.h_ptResVpt_lcalib = ROOT.TH2F(self.name + '_ptResVpt_lcalib', '',
                                           100,0,100, 
                                           100, -1.5, 1.5)
        self.h_ptResVpt_etacalib = ROOT.TH2F(self.name + '_ptResVpt_etacalib', '',
                                             100,0,100, 
                                             100, -1.5, 1.5)

        
        
        self.h_energyResp_raw = ROOT.TH1F(self.name+'_energyResp_raw; E^{L1}/E^{GEN}', '', 200, 0, 2)
        self.h_energyResp_lcalib = ROOT.TH1F(self.name+'_energyResp_lcalib; E^{L1}/E^{GEN}', '', 200, 0, 2)
        self.h_energyResp_etacalib = ROOT.TH1F(self.name+'_energyResp_etacalib; E^{L1}/E^{GEN}', '', 200, 0, 2)

        self.h_energyRes_raw = ROOT.TH1F(self.name+'_energyRes_raw; (E^{L1}-E^{GEN})/E^{GEN}', '', 100, -1.5, 1.5)
        self.h_energyRes_lcalib = ROOT.TH1F(self.name+'_energyRes_lcalib; (E^{L1}-E^{GEN})/E^{GEN}', '', 100, -1.5, 1.5)
        self.h_energyRes_etacalib = ROOT.TH1F(self.name+'_energyRes_etacalib; (E^{L1}-E^{GEN})/E^{GEN}', '', 100, -1.5, 1.5)

        
        self.h_energyResVeta_raw      = ROOT.TH2F(self.name+'_energyResVeta_raw; |#eta|; (E^{L1}-E^{GEN})/E^{GEN}', '', 50, 1.5, 3, 100, -1.5, 1.5)
        self.h_energyResVeta_lcalib   = ROOT.TH2F(self.name+'_energyResVeta_lcalib; |#eta|;  (E^{L1}-E^{GEN})/E^{GEN}', '', 50, 1.5, 3, 100, -1.5, 1.5)
        self.h_energyResVeta_etacalib = ROOT.TH2F(self.name+'_energyResVeta_etacalib; |#eta|;  (E^{L1}-E^{GEN})/E^{GEN}', '', 50, 1.5, 3, 100, -1.5, 1.5)

        
        histos.BaseResoHistos.__init__(self, name, root_file)        
        
    def fill_df(self, df):
        rnp.fill_hist(self.h_energyResVenergy_raw, df[['gen_energy', 'uncalib_res']])
        rnp.fill_hist(self.h_energyResVenergy_lcalib, df[['gen_energy', 'lcalib_res']])
        rnp.fill_hist(self.h_energyResVenergy_etacalib, df[['gen_energy', 'eta_lcalib_res']])

        rnp.fill_hist(self.h_ptResVpt_raw, df[['gen_pt', 'uncalib_res_pt']])
        rnp.fill_hist(self.h_ptResVpt_lcalib, df[['gen_pt', 'lcalib_res_pt']])
        rnp.fill_hist(self.h_ptResVpt_etacalib, df[['gen_pt', 'eta_lcalib_res_pt']])
        
        rnp.fill_hist(self.h_energyResp_raw, df.uncalib_energy_nl0/df.gen_energy)
        rnp.fill_hist(self.h_energyResp_lcalib, df.lcalib_energy/df.gen_energy)
        rnp.fill_hist(self.h_energyResp_etacalib, df.eta_lcalib_energy/df.gen_energy)

        rnp.fill_hist(self.h_energyRes_raw, df.uncalib_res)
        rnp.fill_hist(self.h_energyRes_lcalib, df.lcalib_res)
        rnp.fill_hist(self.h_energyRes_etacalib, df.eta_lcalib_res)

        rnp.fill_hist(self.h_energyResVeta_raw, df[['cl_abseta', 'uncalib_res']])
        rnp.fill_hist(self.h_energyResVeta_lcalib, df[['cl_abseta', 'lcalib_res']])
        rnp.fill_hist(self.h_energyResVeta_etacalib, df[['cl_abseta', 'eta_lcalib_res']])
        
class HWrapper(object):
    def __init__(self, histo):
        self.histo = histo
    
    def get(self, debug=False):
        return self.histo


In [29]:
#compute resolutions
# eta_uncalib_energy_nl0
# eta_lcalib_energy
tree_data['uncalib_res'] = (tree_data.uncalib_energy_nl0 - tree_data.gen_energy)/tree_data.gen_energy
tree_data['lcalib_res'] = (tree_data.lcalib_energy - tree_data.gen_energy)/tree_data.gen_energy
tree_data['eta_uncalib_res'] = (tree_data.eta_uncalib_energy_nl0 - tree_data.gen_energy)/tree_data.gen_energy
tree_data['eta_lcalib_res'] = (tree_data.eta_lcalib_energy - tree_data.gen_energy)/tree_data.gen_energy

tree_data['uncalib_res_pt'] = (tree_data.uncalib_pt_nl0 - tree_data.gen_pt)/tree_data.gen_pt
tree_data['lcalib_res_pt'] = (tree_data.lcalib_pt - tree_data.gen_pt)/tree_data.gen_pt
tree_data['eta_uncalib_res_pt'] = (tree_data.eta_uncalib_pt_nl0 - tree_data.gen_pt)/tree_data.gen_pt
tree_data['eta_lcalib_res_pt'] = (tree_data.eta_lcalib_pt - tree_data.gen_pt)/tree_data.gen_pt




In [30]:

sample = 'ele-V9'
pu = 'PU200'

sel_df = tree_data[(tree_data.smp == sample) &
                   (tree_data.pu == pu) &
                   (tree_data.tp == 'HMvDR') &
                   (tree_data.tp_sel == 'Em') &
                   (tree_data.gen_sel == 'GENEtaBC')]

In [34]:
hplot = HPlot(samples, labels_dict)

for smp in samples:
    print ""
    print '------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label)
    calib_table = calib_table_by_sample[smp.type]
    for tp in tps:
        for gen_sel in ['GENEtaBC', 'GENEtaD', 'GENEtaBCD']:
            for tp_sel in ['Em']:
                print 'TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel)
                hres = EnergyRes(name='{}_{}_{}_{}_{}'.format(smp.type, smp.label, tp, tp_sel, gen_sel))
    
                sel_df = tree_data[(tree_data.smp == smp.type) &
                   (tree_data.pu == smp.label) &
                   (tree_data.tp == tp) &
                   (tree_data.tp_sel == tp_sel) &
                   (tree_data.gen_sel == gen_sel)]

                
                
                hres.fill_df(sel_df)

                hplot.data = hplot.data.append({'sample': smp.type,
                                       'pu': smp.label,
                                       'tp': tp,
                                       'tp_sel': tp_sel,
                                       'gen_sel': gen_sel,
                                       'classtype': EnergyRes,
                                       'histo': HWrapper(hres),},
                                       ignore_index=True)
   


------ SAMPLE: photons-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD

------ SAMPLE: ele-V9, PU: PU0
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD

------ SAMPLE: ele-V9, PU: PU200
TP: HMvDR sel: Em, gen_sel: GENEtaBC
TP: HMvDR sel: Em, gen_sel: GENEtaD
TP: HMvDR sel: Em, gen_sel: GENEtaBCD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBC
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaD
TP: HMvDRshapeDr sel: Em, gen_sel: GENEtaBCD


In [35]:
hplot.data[:10]

sample   pu            tp tp_sel    gen_sel           classtype  \
0  photons-V9  PU0         HMvDR     Em   GENEtaBC  __main__.EnergyRes   
1  photons-V9  PU0         HMvDR     Em    GENEtaD  __main__.EnergyRes   
2  photons-V9  PU0         HMvDR     Em  GENEtaBCD  __main__.EnergyRes   
3  photons-V9  PU0  HMvDRshapeDr     Em   GENEtaBC  __main__.EnergyRes   
4  photons-V9  PU0  HMvDRshapeDr     Em    GENEtaD  __main__.EnergyRes   
5  photons-V9  PU0  HMvDRshapeDr     Em  GENEtaBCD  __main__.EnergyRes   
6      ele-V9  PU0         HMvDR     Em   GENEtaBC  __main__.EnergyRes   
7      ele-V9  PU0         HMvDR     Em    GENEtaD  __main__.EnergyRes   
8      ele-V9  PU0         HMvDR     Em  GENEtaBCD  __main__.EnergyRes   
9      ele-V9  PU0  HMvDRshapeDr     Em   GENEtaBC  __main__.EnergyRes   

                                       histo  
0  <__main__.HWrapper object at 0x1b51bc550>  
1  <__main__.HWrapper object at 0x1b51bc450>  
2  <__main__.HWrapper object at 0x1b51bc810>  
3  <__main__.HWrapper object at 0x1b51bc890>  
4  <__main__.HWrapper object at 0x1b51bc4d0>  
5  <__main__.HWrapper object at 0x1b51bc850>  
6  <__main__.HWrapper object at 0x1b51bca90>  
7  <__main__.HWrapper object at 0x1b51e4290>  
8  <__main__.HWrapper object at 0x1b51bc350>  
9  <__main__.HWrapper object at 0x1b51bcc10>

In [36]:
hplot.data.tp.unique()

array(['HMvDR', 'HMvDRshapeDr'], dtype=object)

In [37]:
hplot.labels_dict

{'': '',
 'DEF': 'dRC3d',
 'DEF2D': 'dRC2d',
 'DEF2DTrue': 'dRC2d True',
 'DEFCalib': 'dRC3d calib.',
 'DEFMerged': 'dRC3d merged',
 'DEFNC': 'dRC3d NewTh',
 'EG': 'EG',
 'EGALL': 'EG all',
 'EGBRL': 'EG barrel',
 'EGq2': 'hwQual 2',
 'EGq2EtaBC': 'hwQual 2, 1.52 < |#eta^{L1}| <= 2.4',
 'EGq2EtaBCD': 'hwQual 2, 1.52 < |#eta^{L1}| <= 2.8',
 'EGq2EtaBCDE': 'hwQual 2, 1.52 < |#eta^{L1}| < 3',
 'EGq2EtaBCDEM1': 'hwQual 2, 1.52 < |#eta^{L1}| < 3, |#Delta#phi| <0.08 & #DeltaR < 0.07',
 'EGq2EtaBCDEM1P10': 'hwQual 2, 1.52 < |#eta^{L1}| < 3, |#Delta#phi| <0.08 & #DeltaR < 0.07 & p_{T}^{trk} > 10GeV',
 'EGq2EtaBCDEM1P2': 'hwQual 2, 1.52 < |#eta^{L1}| < 3, |#Delta#phi| <0.08 & #DeltaR < 0.07 & p_{T}^{trk} > 2GeV',
 'EGq2EtaBCDEM1P5': 'hwQual 2, 1.52 < |#eta^{L1}| < 3, |#Delta#phi| <0.08 & #DeltaR < 0.07 & p_{T}^{trk} > 5GeV',
 'EGq2EtaBCDM1': 'hwQual 2, 1.52 < |#eta^{L1}| <= 2.8, |#Delta#phi| <0.08 & #DeltaR < 0.07',
 'EGq2EtaBCDM1P10': 'hwQual 2, 1.52 < |#eta^{L1}| <= 2.8, |#Delta#phi| <0.08 & 

In [38]:
hfd = hplot.get_histo('pippo', 'ele-V9', ['PU0'], ['HMvDRcylind2p5'], 'Em', 'GENEtaBC')

print hfd[0]
print hfd[1]
print hfd[2]




No match found for: pu: ['PU0'], tp: ['HMvDRcylind2p5'], tp_sel: Em, gen_sel: GENEtaBC, classtype: pippo
None
None
None


In [39]:
print hfd[2]


None


## Comparison of the calibration sets for different selections

In [111]:
tp = 'HMvDRshapeDr'
tp_sel = 'Em'

calib = calib_df[(calib_df.smp == calib_sample) &
                 (calib_df.pu == calib_pu) &
                 (calib_df.tp == tp) &
                 (calib_df.tp_sel == tp_sel) &
                 (calib_df.gen_sel == calib_eta)]
calib_values = calib.layer_calib.values[0]
print 'Layer calib values: {}'.format([float("{0:0.2f}".format(i)) for i in calib_values ])
# print calib_values


Layer calib values: [0.0, 2.0, 0.74, 1.09, 1.18, 0.91, 1.1, 0.5, 1.51, 1.13, 0.93, 0.72, 1.29, 1.94]


In [ ]:
[0.0, 1.4, 0.84, 1.14, 1.0, 0.98, 1.03, 1.03, 1.03, 0.92, 0.99, 0.93, 1.45, 1.88]

In [112]:
tp = 'HMvDRshapeDr'
tp_sel = 'Em'
eta = 1.5653

calib = eta_calib_df[(eta_calib_df.smp == eta_calib_sample) &
                                 (eta_calib_df.pu == eta_calib_pu) &
                                   (eta_calib_df.tp == tp) &
                                   (eta_calib_df.tp_sel == tp_sel) &
                                   (eta_calib_df.gen_sel == eta_calib_eta)]
calib_values = calib.eta_calib_1.values[0]
print calib_values

print calib_values[1]+eta*calib_values[0]


eta_corr_function = ROOT.TF1('HMvDRshapeDr_eta_corr', 'pol1', 1.5, 3)
eta_corr_function.SetParameters(calib_values[1], calib_values[0])
canvas = newCanvas()
canvas.cd()
eta_corr_function.Draw()
canvas.Draw()

(-34.431755, 66.722359)
12.8263324989


In [42]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBCD')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResVeta_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResVeta_lcalib)
labels_new.append('l-calib')                                             

# hsets_new.append(hsets[0].h_energyResVeta_etacalib)
# labels_new.append('eta-calib')                                             


# hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaBC')
# hsets_new.append(hsets[0].h_energyRes_raw)
# labels_new.append('un-calib L1 menu OLD')                                             

draw(hsets_new, labels_new,  text=text, options='COLZ', norm=True, do_profile=True, min_y=-0.5, max_y=0.5, h_lines=[0.])


In [43]:
hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBCD')
hsets_new = []
labels_new = []


# hsets_new.append(hsets[0].h_energyResVeta_raw)
# labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResVeta_lcalib)
labels_new.append('l-calib')                                             

hsets_new.append(hsets[0].h_energyResVeta_etacalib)
labels_new.append('eta-calib')                                             


# hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaBC')
# hsets_new.append(hsets[0].h_energyRes_raw)
# labels_new.append('un-calib L1 menu OLD')                                             

draw(hsets_new, labels_new,  text=text, options='COLZ', norm=True, do_profile=True, min_y=-0.5, max_y=0.5, h_lines=[0])


In [44]:
sample='photons-V9'

In [45]:
for tp in tps:
#     for tp_sel in tp_select[tp]:
        for gen_sel in ['GENEtaBC']:
            hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], tp, ['all', 'Em'], gen_sel)
            draw(hsets, labels,  text=text, min_y=0., max_y=2.)

No match found for: pu: ['PU0'], tp: HMvDR, tp_sel: ['all', 'Em'], gen_sel: GENEtaBC, classtype: pippo


TypeError: 'NoneType' object is not iterable

In [ ]:
for tp in tps:
#     for tp_sel in tp_select[tp]:
#         for gen_sel in ['GENEtaBC']:
            hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], tp, ['Em'], ['GENEtaBC', 'GENEtaD', 'GENEtaBCD'])
            draw(hsets, labels,  text=text, min_y=0., max_y=2.)

In [ ]:

hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind5', 'HMvDRshape', 'HMvDRshapeDr'], 'Em', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=10., h_lines=[1.])

In [ ]:

hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind5', 'HMvDRcylind5Calib','HMvDRcylind5Calib1'], 'Em', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:

hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind10', 'HMvDRcylind10Calib','HMvDRcylind10Calib1'], 'Em', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRshape', 'HMvDRshapeCalib','HMvDRshapeCalib1'], 'Em', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:

hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind2p5Calib','HMvDRcylind2p5Calib1'], 'Em', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind5','HMvDRcylind10'], 'Em', 'GENEtaBCPt10')
draw(hsets, labels,  text=text, min_y=0., max_y=10., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind5','HMvDRcylind10'], 'Em', 'GENEtaBCPt40')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind5','HMvDRcylind10'], 'all', 'GEN')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind5','HMvDRcylind10'], 'all', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind2p5', 'HMvDRcylind5','HMvDRcylind10'], 'all', 'GENEtaBC')
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
for tp in tps:
    for gen_sel in ['GENEtaBC', 'GENEtaBCPt10', 'GENEtaBCPt20', 'GENEtaBCPt40']:
        hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], tp, ['all', 'Em'], gen_sel)
        draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
for tp in tps:
    hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], tp, ['Em'], ['GENEtaBC', 'GENEtaBCPt10', 'GENEtaBCPt20', 'GENEtaBCPt40'])
    draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
for tp in tps:
    hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], tp, ['all'], ['GENEtaBC', 'GENEtaBCPt10', 'GENEtaBCPt20', 'GENEtaBCPt40'])
    draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
hsets, labels, text = hplot.get_histo('pippo', sample, ['PU0'], ['HMvDRcylind10'], ['all', 'Em'], ['GENEtaBC'])
draw(hsets, labels,  text=text, min_y=0., max_y=2., h_lines=[1.])

In [ ]:
len([1.527]+[1.]*12+[1.98])

## Energy Resolution

### Plot response plots

In [46]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBC')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyRes_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyRes_lcalib)
labels_new.append('l-calib')                                             

hsets_new.append(hsets[0].h_energyRes_etacalib)
labels_new.append('eta-calib')                                             


hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaBC')
hsets_new.append(hsets[0].h_energyRes_raw)
labels_new.append('un-calib L1 menu OLD')                                             

draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [47]:


hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaD')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyRes_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyRes_lcalib)
labels_new.append('l-calib')                                             

hsets_new.append(hsets[0].h_energyRes_etacalib)
labels_new.append('eta-calib')                                             


hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaD')
hsets_new.append(hsets[0].h_energyRes_raw)
labels_new.append('un-calib L1 menu OLD')                                             

draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [48]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBC')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResp_lcalib)
labels_new.append('l-calib')                                             

hsets_new.append(hsets[0].h_energyResp_etacalib)
labels_new.append('eta-calib')                                             


hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaBC')
hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib L1 menu OLD')                                             

draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [49]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaD')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResp_lcalib)
labels_new.append('l-calib')                                             

hsets_new.append(hsets[0].h_energyResp_etacalib)
labels_new.append('eta-calib')                                             


hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaD')
hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib L1 menu OLD')                                             

draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [51]:
hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBCD')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResp_etacalib)
labels_new.append('eta-calib backport')                                             

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDR'], 'Em', 'GENEtaBC')
hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib L1 menu')                                             



draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [52]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaD')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResp_etacalib)
labels_new.append('eta-calib')                                             




draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [53]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBC')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResp_lcalib)
labels_new.append('layer-weights')                                             

# hsets_new.append(hsets[0].h_energyResp_etacalib)
# labels_new.append('eta-corr')                                             

hsets_new.append(hsets[0].h_energyResp_etacalib)
labels_new.append('layer-weights+eta-corr')                                             



draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


In [54]:

hsets, labels, text = hplot.get_histo(EnergyRes, ['ele-V9'], ['PU200'], ['HMvDRshapeDr'], 'Em', 'GENEtaBCD')
hsets_new = []
labels_new = []


hsets_new.append(hsets[0].h_energyResp_raw)
labels_new.append('un-calib')                                             

hsets_new.append(hsets[0].h_energyResp_lcalib)
labels_new.append('layer-weights')                                             

hsets_new.append(hsets[0].h_energyResp_etacalib)
labels_new.append('layer-weights+eta-corr')                                             



draw(hsets_new, labels_new,  text=text, options='hist', norm=True)


### Fit resolution plots

In [55]:
# %load ./python/utilities.py
import uuid
import ROOT
from drawingTools import draw
import math

def effSigma(hist):
    xaxis = hist.GetXaxis()
    nb = xaxis.GetNbins()
    if nb < 10:
        print "effsigma: Not a valid histo. nbins = {}".format(nb)
        return -1
    
    bwid = xaxis.GetBinWidth(1)
    if bwid == 0:
        print "effsigma: Not a valid histo. bwid = {}".format(bwid)
        return -1

    xmax = xaxis.GetXmax()
    xmin = xaxis.GetXmin()
    ave = hist.GetMean()
    rms = hist.GetRMS()
    
#     print 'xmax: {}, xmin: {}, ave: {}, rms: {}'.format(xmax, xmin, ave, rms)
    
    total=0.
    for i in range(0, nb+2):
        total+=hist.GetBinContent(i)
    
    if total < 100.:
        print "effsigma: Too few entries {}".format(total)
        return -1

    ierr = 0
    ismin = 999
  
    rlim = 0.683*total
    # Set scan size to +/- rms
    nrms = int(rms/(bwid))
    if nrms > nb/10:
        # could be tuned
        nrms = nb/10
    
    widmin = 9999999.
    # scan the window center
    for iscan in range(-nrms, nrms+1):
        ibm = int((ave-xmin)/bwid+1+iscan)
        x = (ibm-0.5)*bwid+xmin;
        xj = x
        xk = x
        jbm = ibm;
        kbm = ibm;
        bin = hist.GetBinContent(ibm)
        total = bin
        for j in range(1, nb):
            if jbm < nb: 
                jbm += 1
                xj += bwid
                bin = hist.GetBinContent(jbm)
                total += bin
                if total > rlim:
                    break
            else:
                ierr = 1
            if kbm > 0: 
                kbm -= 1
                xk -= bwid
                bin = hist.GetBinContent(kbm)
                total += bin;
                if total > rlim:
                    break
            else:
                ierr = 1
        dxf = (total-rlim)*bwid/bin
        wid = (xj-xk+bwid-dxf)*0.5
        if wid < widmin:
            widmin=wid
            ismin=iscan
  
    if ismin == nrms or ismin == -nrms:
        ierr = 3
    if ierr != 0:
        print "effsigma: Error of type {}".format(ierr)
  
    return widmin
  

def quantiles(yswz, zeroSuppress=True):
    ys = [y for y in yswz if y > 0] if zeroSuppress else yswz[:]
    if len(ys) < 3: return (0,0,0)
    ys.sort()
    ny = len(ys)
    median = ys[ny/2]
   #if ny > 400e9:
   #    u95 = ys[min(int(ceil(ny*0.975)),ny-1) ]
   #    l95 = ys[int(floor(ny*0.025))]
   #    u68 = 0.5*(median+u95)
   #    l68 = 0.5*(median+l95)
    if ny > 20:
        u68 = ys[min(int(math.ceil(ny*0.84)),ny-1) ]
        l68 = ys[int(math.floor(ny*0.16))]
    else:
        rms = math.sqrt(sum((y-median)**2 for y in ys)/ny)
        u68 = median + rms
        l68 = median - rms
    return (median,l68,u68)


def gausstailfit_wc(name, project_hist, bin_limits):
    global cache
    if cache is not None and not cache[(cache.h_name == name) & (cache.bin_limits == bin_limits)].empty:
        print 'READ cached fit results h_name: {}, bin_limits: {}'.format(name, bin_limits)
#         print cache[(cache.h_name == name) & (cache.bin_limits == bin_limits)].results
        return cache[(cache.h_name == name) & (cache.bin_limits == bin_limits)].results.values[0]

    max_bin = project_hist.GetMaximumBin()
    max_value = project_hist.GetBinCenter(max_bin)
    rms_value = project_hist.GetRMS()
    max_y = project_hist.GetMaximum()
#     print max_bin, max_value, rms_value

    def gausstail(x, p):
        #         // [Constant] * ROOT::Math::crystalball_function(x, [Alpha], [N], [Sigma], [Mean])
        return p[0] * ROOT.Math.crystalball_function(x[0], p[3], p[4], p[2], p[1])

    fitf = ROOT.TF1('gausstail', gausstail, -1.5, 1.5, 5)
    fitf.SetParNames('norm', 'mean', 'sigma', 'alpha', 'n')
#     fitf.FixParameter(0, 1.)
    fitf.SetParLimits(1, max_value-0.04, max_value+0.04)

    fitf.SetParameters(max_y, max_value, rms_value, 1, 1)
    draw([project_hist], labels=['fit'], text=name)
    stuff.append(fitf)
    project_hist.Draw("same")
#     c.Draw()
#     print '   name: {}, y_max = {}, max_value = {}, RMS = {}'.format(name, max_y, max_value, rms_value)
    result = project_hist.Fit('gausstail', 'QERLS+')
    result.Print()
#     print '   norm = {}, reso_mean = {}, reso_sigma = {}, alpha = {}, n = {}'.format(result.GetParams()[0], result.GetParams()[1], result.GetParams()[2], result.GetParams()[3], result.GetParams()[4])
#     func = project_hist.GetFunction("gaus")
    # print '   NDF = {}, chi2 = {}, prob = {}'.format(fitf.GetNDF(), fitf.GetChisquare(), fitf.GetProb())

    if cache is not None:
        cache = cache.append({'h_name': name,
                              'bin_limits': bin_limits,
                              'results': result}, ignore_index=True)
#         print cache

    return result

def effective_sigma_energy(project_hist):
    eff_sigma = effSigma(project_hist)
    bin_values = [project_hist.GetBinContent(bin) for bin in range(1, project_hist.GetNbinsX()+1)]
    return (eff_sigma,)


def gausstailfit_energy(project_hist):
    max_bin = project_hist.GetMaximumBin()
    max_value = project_hist.GetBinCenter(max_bin)
    rms_value = project_hist.GetRMS()
    max_y = project_hist.GetMaximum()

    def gausstail(x, p):
        return p[0] * ROOT.Math.crystalball_function(x[0], p[3], p[4], p[2], p[1])

    fitf = ROOT.TF1('gausstail', gausstail, -1.0, 0.5, 5)
    fitf.SetParNames('norm', 'mean', 'sigma', 'alpha', 'n')
#     fitf.FixParameter(0, 1.)
    fitf.SetParLimits(1, max_value-0.04, max_value+0.04)
    fitf.SetParameters(max_y, max_value, rms_value, 1, 1)
    stuff.append(fitf)
    project_hist.Draw()
#     c.Draw()
#     print '   y_max = {}, max_value = {}, RMS = {}'.format(max_y, max_value, rms_value)
    result = project_hist.Fit('gausstail', 'QERLS+')
    result.Print()
#     print '   norm = {}, reso_mean = {}, reso_sigma = {}, alpha = {}, n = {}'.format(result.GetParams()[0], 
#                                                                                      result.GetParams()[1], 
#                                                                                      result.GetParams()[2], 
#                                                                                      result.GetParams()[3], 
#                                                                                      result.GetParams()[4])
    return result.GetParams()[0], result.GetParams()[1], result.GetParams()[2], result.GetParams()[3], result.GetParams()[4]


def computeResolution(histo2d,
                      bin_limits,
                      y_axis_range,
                      fit_function,
                      result_index,
                      cache=None):
    global stuff
    
    def get_results(histo_name,
                    project_hist,
                    bin_limits,
                    fit_function,
                    cache=None):
        if cache is not None:
            if not cache[(cache.h_name == histo_name) &
                         (cache.bin_limits == bin_limits) &
                         (cache.fit_function == fit_function)].empty:
                print 'READ cached fit results h_name: {}, bin_limits: {}, fit_function: {}'.format(histo_name, 
                                                                                                    bin_limits,
                                                                                                    fit_function)
                return cache[(cache.h_name == histo_name) & 
                            (cache.bin_limits == bin_limits) &
                            (cache.fit_function == fit_function)].results.values[0]
            else:
                print "No ENTRY in CACHE"
                result = fit_function(project_hist)
                cache.loc[cache.shape[0]+1] = {'h_name': histo_name,
                                      'bin_limits': bin_limits,
                                      'fit_function': fit_function,
                                      'results': result}
                return result
        return fit_function(project_hist)
            

    
    h2d = histo2d.Clone()
    h2d.GetYaxis().SetRangeUser(y_axis_range[0], y_axis_range[1])

    x, y, ex_l, ex_h, ey_l, ey_h = [], [], [], [], [], []
    print '-----------------------'
    for x_bin_low, x_bin_high in bin_limits:
        y_proj = h2d.ProjectionY(uuid.uuid4().hex[:6]+'_y', x_bin_low, x_bin_high)
        stuff.append(y_proj)
        x_low = h2d.GetXaxis().GetBinLowEdge(x_bin_low)
        x_high = h2d.GetXaxis().GetBinUpEdge(x_bin_high)
#         print 'x_low: {} x_high: {}'.format(x_low, x_high)
        draw([y_proj], labels=['fit'], text='BIN: ({}, {}) = ({}, {}) GeV, RES: {}'.format(
                                            x_bin_low, x_bin_high, x_low, x_high, 0))

        fit_result = get_results(histo2d.GetName(),
                                 y_proj,
                                 (x_bin_low, x_bin_high),
                                 fit_function,
                                 cache)
#         draw([y_proj], labels=['fit'], text='BIN: ({}, {}) = ({}, {}) GeV, RES: {}'.format(
#                                             x_bin_low, x_bin_high, x_low, x_high, fit_result[result_index]))

        h2d.SetAxisRange(x_low, x_high)
        x_mean = h2d.GetMean()
        x.append(x_mean)
        ex_l.append(0)
        ex_h.append(0)
        y.append(fit_result[result_index])
        ey_l.append(0)
        ey_h.append(0)
    return x, y, ex_l, ex_h, ey_l, ey_h

        
def computeEResolution(h2d_orig,
                       bins_limits=[(3, 6), (7, 12), (13, 23), (24, 34), (35, 49), (50, 100)],
                       cache=None):
    global stuff
    h2d = h2d_orig.Clone()
    h2d.GetYaxis().SetRangeUser(-100, 100)
    x, y, ex_l, ex_h, ey_l, ey_h = [], [], [], [], [], []
    print '-----------------------'
    for x_bin_low, x_bin_high in bins_limits:
        y_proj = h2d.ProjectionY(uuid.uuid4().hex[:6]+'_y', x_bin_low, x_bin_high)
        stuff.append(y_proj)
        x_low = h2d.GetXaxis().GetBinLowEdge(x_bin_low)
        x_high = h2d.GetXaxis().GetBinUpEdge(x_bin_high)
#         print 'x_low: {} x_high: {}'.format(x_low, x_high)
#         fit_result = gausstailfit(h2d_orig.GetName(), y_proj)
        fit_result = gausstailfit_wc(h2d_orig.GetName(), y_proj, (x_bin_low, x_bin_high))
        h2d.SetAxisRange(x_low, x_high)
        x_mean = h2d.GetMean()
#         print 'mean: {}'.format(x_mean)
    #     x_value = h2d.GetXaxis().GetBinCenter(x_bin)
    #     x_err_min = x_value - h2d.GetXaxis().GetBinLowEdge(x_bin)
    #     x_err_plus = h2d.GetXaxis().GetBinUpEdge(x_bin) - x_value

        x.append(x_mean)
        ex_l.append(0)
        ex_h.append(0)
        y.append(fit_result.GetParams()[2])

#         y.append(fit_result.GetParams()[2]/x_mean)
        ey_l.append(0)
        ey_h.append(0)
    return x, y, ex_l, ex_h, ey_l, ey_h


def computeEResolutionMean(h2d_orig,
                           bins_limits=[(3, 6), (7, 12), (13, 23), (24, 34), (35, 49), (50, 100)],
                           cache=None):
    h2d = h2d_orig.Clone()
    h2d.GetYaxis().SetRangeUser(-100, 100)
    x, y, ex_l, ex_h, ey_l, ey_h = [], [], [], [], [], []
    print '-----------------------'
    for x_bin_low, x_bin_high in bins_limits:
        y_proj = h2d.ProjectionY(uuid.uuid4().hex[:6]+'_y', x_bin_low, x_bin_high)
        stuff.append(y_proj)
        x_low = h2d.GetXaxis().GetBinLowEdge(x_bin_low)
        x_high = h2d.GetXaxis().GetBinUpEdge(x_bin_high)
        print 'x_low: {} x_high: {}'.format(x_low, x_high)
#         fit_result = gausstailfit(h2d_orig.GetName(), y_proj)
        fit_result = gausstailfit_wc(h2d_orig.GetName(), y_proj, (x_bin_low, x_bin_high))

        h2d.SetAxisRange(x_low, x_high)
        x_mean = h2d.GetMean()
#         print 'mean: {}'.format(x_mean)
    #     x_value = h2d.GetXaxis().GetBinCenter(x_bin)
    #     x_err_min = x_value - h2d.GetXaxis().GetBinLowEdge(x_bin)
    #     x_err_plus = h2d.GetXaxis().GetBinUpEdge(x_bin) - x_value

        x.append(x_mean)
        ex_l.append(0)
        ex_h.append(0)

        y.append(fit_result.GetParams()[1])
        ey_l.append(0)
        ey_h.append(0)
    return x, y, ex_l, ex_h, ey_l, ey_h


In [56]:
# run this cell to clean the cache of the fit results
cache = pd.DataFrame(columns=['h_name', 'bin_limits', 'fit_function', 'results'])


In [57]:
cache2 = pd.DataFrame(columns=['h_name', 'bin_limits', 'fit_function', 'results'])


#### EtaBC fits

In [75]:
energy_bins = [(3, 6), (7, 12), (13, 23), (24, 34), (35, 49), (50, 100)]

In [85]:
new_bins = [(7, 10), (11, 14), (15, 18), (19, 24), (25, 30), (31, 36), (37, 42), (43, 48), (49, 59), 
            (60, 70), (71, 81), (82, 100)]


##### photons

In [77]:
for sample in ['photons-V9']:
    for tp in tps:
        for pu in ['PU0']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
            for his in hsets:
                his.h_energyResVenergy_raw_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (50, 100), fit_function: <function 

In [78]:
for sample in ['photons-V9']:
    for tp in tps:
        for pu in ['PU0']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
            for his in hsets:
                his.h_energyResVenergy_lcalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))


-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 

In [79]:
for sample in ['photons-V9']:
    for tp in tps:
        for pu in ['PU0']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
            for his in hsets:
                his.h_energyResVenergy_etacalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))


-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (35, 49), fit_function: <function gausstailfit_

In [80]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
            for his in hsets:
                his.h_energyResVenergy_raw_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_raw, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit result

In [81]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
            for his in hsets:
                his.h_energyResVenergy_lcalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_lcalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ ca

In [82]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
            for his in hsets:
                his.h_energyResVenergy_etacalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBC_energyResVenergy_etacalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d7

In [83]:
dm = DrawMachine(rleg_config)
hsets, labels, text = hplot.get_histo(EnergyRes, 'photons-V9', 'PU0', ['HMvDRshapeDr'], ['Em'], 'GENEtaBC', debug=False)

dm.addHistos([his.g_energyResVenergy_raw_gaussSigma for his in hsets], ['#sigma gauss'])
dm.addHistos([his.g_energyResVenergy_raw_effSigma for his in hsets], ['eff #sigma'])

dm.draw(text=text, options='COLZ', y_min=0., y_max=0.1)




#             draw([his.h_energyResVenergy_raw_graph('sigmaEOENew2', '#sigma_{E}/E', lambda h2d: computeResolution(histo2d=h2d,
#                                                                                                                 bin_limits=[(3, 6), (7, 12), (13, 23), (24, 34), (35, 49), (50, 100)],
#                                                                                                                 y_axis_range=(-100, 100),
#                                                                                                                 fit_function=effective_sigma_energy,
#                                                                                                                 result_index=0,
#                                                                                                                 cache=cache2)) for his in hsets], labels, text=text, options='COLZ', min_y=0., max_y=0.1)


In [68]:
cache2

h_name bin_limits  \
1   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)   
2   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)   
3   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)   
4   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)   
5   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)   
6   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)   
7   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)   
8   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)   
9   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)   
10  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)   
11  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)   
12  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)   
13  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)   
14  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)   
15  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)   
16  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)   
17  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)   
18  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)   
19  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)   
20  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)   
21  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)   
22  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)   
23  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)   
24  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)   
25  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)   
26  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)   
27  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)   
28  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)   
29  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)   
30  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)   
31  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)   
32  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)   
33  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)   
34  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)   
35  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)   
36  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)   
37  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)   
38  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)   
39  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)   
40  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)   
41  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)   
42  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)   
43  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)   
44  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)   
45  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)   
46  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)   
47  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)   
48  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)   

                                        fit_function  \
1      <function gausstailfit_energy at 0x1b5410d70>   
2      <function gausstailfit_energy at 0x1b5410d70>   
3      <function gausstailfit_energy at 0x1b5410d70>   
4      <function gausstailfit_energy at 0x1b5410d70>   
5      <function gausstailfit_energy at 0x1b5410d70>   
6      <function gausstailfit_energy at 0x1b5410d70>   
7   <function effective_sigma_energy at 0x1b5410f50>   
8   <function effective_sigma_energy at 0x1b5410f50>   
9   <function effective_sigma_energy at 0x1b5410f50>   
10  <function effective_sigma_energy at 0x1b5410f50>   
11  <function effective_sigma_energy at 0x1b5410f50>   
12  <function effective_sigma_energy at 0x

In [69]:
cache

h_name bin_limits fit_function  \
0   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)          NaN   
1   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)          NaN   
2   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)          NaN   
3   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)          NaN   
4   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)          NaN   
5   photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)          NaN   
6   photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)          NaN   
7   photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)          NaN   
8   photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)          NaN   
9   photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)          NaN   
10  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)          NaN   
11  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)          NaN   
12  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)          NaN   
13  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)          NaN   
14  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)          NaN   
15  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)          NaN   
16  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)          NaN   
17  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)          NaN   
18  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)          NaN   
19  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)          NaN   
20  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)          NaN   
21  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)          NaN   
22  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)          NaN   
23  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)          NaN   
24  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...     (3, 6)          NaN   
25  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...    (7, 12)          NaN   
26  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (13, 23)          NaN   
27  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (24, 34)          NaN   
28  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...   (35, 49)          NaN   
29  photons-V9_PU0_HMvDR_Em_GENEtaBC_energyResVene...  (50, 100)          NaN   
30  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...     (3, 6)          NaN   
31  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...    (7, 12)          NaN   
32  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (13, 23)          NaN   
33  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (24, 34)          NaN   
34  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...   (35, 49)          NaN   
35  photons-V9_PU0_HMvDRshapeDr_Em_GENEtaBC_energy...  (50, 100)          NaN   

                                          results  
0   <ROOT.TFitResultPtr object at 0x7fc0b99c8e70>  
1   <ROOT.TFitResultPtr object at 0x7fc0b9b85c60>  
2   <ROOT.TFitResultPtr object at 0x7fc0b9c0bcd0>  
3   <ROOT.TFitResultPtr object at 0x7fc0b9a82eb0>  
4   <ROOT.TFitResultPtr object at 0x7fc0b98bccf0>  
5   <ROOT.TFitResultPtr object at 0x7fc0b9d34da0>  
6   <ROOT.TFitResultPtr object at 0x7fc0b9a9fed0>  
7   <ROOT.TFitResultPtr object at 0x7fc0b9c274c0>  
8   <ROOT.TFitResultPtr object at 0x7fc0b9ba31e0>  
9   <ROOT.TFitResultPtr object at 0x7fc0b9c243d0>  
10  <ROOT.TFitResultPtr object at 0x7fc0b9d6e230>  
11  <ROOT.TFitResultPtr object at 0x7fc0b9d3e480>  
12  <ROOT.TFitResultPtr object at 0x7fc0b9bcc660>  
13  <ROOT.TFitResultPtr object at 0x7fc0b9dbcab0>  
14  <ROOT.TFitResultPtr object at 0x7fc0b9bc7840>  
15  <ROOT.TFitResultPtr object at 0x7fc0b9dca980>  
16  <ROOT.TFitResultPtr object at 0x7fc0b9c44520>  
17  <ROOT.TFitResultPtr object at 0x7fc0b9ad73e0>  
18  <ROOT.TFitResultPtr object at 0x7fc0b9be7840>  
19  <ROOT

#### EtaD filts

In [86]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaD', debug=False)
            for his in hsets:
                his.h_energyResVenergy_raw_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_raw, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_raw, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_raw, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_raw, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_raw, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_n

In [87]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaD', debug=False)
            for his in hsets:
                his.h_energyResVenergy_lcalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_lcalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_lcalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_lcalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_lcalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_lcalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached 

In [88]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaD', debug=False)
            for his in hsets:
                his.h_energyResVenergy_etacalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_etacalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_etacalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_etacalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_etacalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaD_energyResVenergy_etacalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
RE

#### EtaBCD

In [89]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBCD', debug=False)
            for his in hsets:
                his.h_energyResVenergy_raw_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_raw_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_raw, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_raw, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_raw, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_raw, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_raw, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit r

In [90]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBCD', debug=False)
            for his in hsets:
                his.h_energyResVenergy_lcalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_lcalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_lcalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_lcalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_lcalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_lcalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_lcalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5410d70>
RE

In [91]:
for sample in ['ele-V9']:
    for tp in tps:
        for pu in ['PU0', 'PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBCD', debug=False)
            for his in hsets:
                his.h_energyResVenergy_etacalib_graph(
                    'gaussSigma', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=2,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'gaussMean', 
                    '#sigma^{gauss}_{E}/E', 
                     lambda h2d: computeResolution(
                         histo2d=h2d,
                         bin_limits=energy_bins,
                         y_axis_range=(-100, 100),
                         fit_function=gausstailfit_energy,
                         result_index=1,
                         cache=cache2))
                his.h_energyResVenergy_etacalib_graph(
                    'effSigma', 
                    '#sigma^{eff.}_{E}/E', 
                   lambda h2d: computeResolution(
                       histo2d=h2d,
                       bin_limits=energy_bins,
                       y_axis_range=(-100, 100),
                       fit_function=effective_sigma_energy,
                       result_index=0,
                       cache=cache2))
                

-----------------------
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
No ENTRY in CACHE
-----------------------
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_etacalib, bin_limits: (3, 6), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_etacalib, bin_limits: (7, 12), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_etacalib, bin_limits: (13, 23), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_etacalib, bin_limits: (24, 34), fit_function: <function gausstailfit_energy at 0x1b5410d70>
READ cached fit results h_name: ele-V9_PU0_HMvDR_Em_GENEtaBCD_energyResVenergy_etacalib, bin_limits: (35, 49), fit_function: <function gausstailfit_energy at 0x1b5

### Draw resolution fit results

In [93]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU0', ['HMvDR','HMvDRCalib', 'HMvDRshapeDr', 'HMvDRshapeDrCalib'], ['Em'], 'GENEtaBC', debug=False)
    draw([his.g_energyResVenergy_raw_gaussMean for his in hsets], labels, text=text, options='L', min_y=-0.5, max_y=0.5)


In [94]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU0', ['HMvDR','HMvDRCalib', 'HMvDRshapeDr', 'HMvDRshapeDrCalib'], ['Em'], 'GENEtaBC', debug=False)
    draw([his.h_energyResVenergy_raw for his in hsets], labels, text=text, options='COLZ', min_y=-50, max_y=50)


In [95]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDR','HMvDRCalib', 'HMvDRshapeDr', 'HMvDRshapeDrCalib'], ['Em'], 'GENEtaBC', debug=False)
    draw([his.g_energyResVenergy_lcalib_gaussMean for his in hsets], labels, text=text, options='COLZ', min_y=-0.5, max_y=0.5, h_lines=[0.])


In [97]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDR','HMvDRCalib', 'HMvDRshapeDr', 'HMvDRshapeDrCalib'], ['Em'], 'GENEtaBC', debug=False)
    draw([his.g_energyResVenergy_etacalib_gaussMean for his in hsets], labels, text=text, options='COLZ', 
         min_y=-0.5, max_y=0.5, h_lines=[0.])


In [99]:
dm = DrawMachine(rleg_config)
hsets, labels, text = hplot.get_histo(EnergyRes, 'ele-V9', 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaBC', debug=False)

# dm.addHistos([his.g_energyResVenergy_raw_sigmaEOE for his in hsets], ['no corr.'])
dm.addHistos([his.g_energyResVenergy_raw_effSigma for his in hsets], ['no corr. effSigma'])

# dm.addHistos([his.g_energyResVenergy_lcalib_sigmaEOE for his in hsets], ['layer-calib.'])
dm.addHistos([his.g_energyResVenergy_lcalib_effSigma for his in hsets], ['layercalib. effSigma'])

# dm.addHistos([his.g_energyResVenergy_etacalib_sigmaEOE for his in hsets], ['eta+layer-calib.'])
dm.addHistos([his.g_energyResVenergy_etacalib_effSigma for his in hsets], ['eta+layercalib. effSigma'])


dm.draw(text=text, options='COLZ', y_min=0., y_max=0.1)



In [100]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaBC', debug=False)
    hset_new = []
    labels_new = []

    hset_new.append(hsets[0].g_energyResVenergy_raw_gaussSigma)
    labels_new.append('no corr.')

    hset_new.append(hsets[0].g_energyResVenergy_lcalib_gaussSigma)
    labels_new.append('layer calib.')

    hset_new.append(hsets[0].g_energyResVenergy_etacalib_gaussSigma)
    labels_new.append('eta+ layer calib.')

    
    draw(hset_new, labels_new, options='L', text=text,  min_y=-0, max_y=0.1)


In [101]:
dm = DrawMachine(rleg_config)
hsets, labels, text = hplot.get_histo(EnergyRes, 'ele-V9', 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaBC', debug=False)

dm.addHistos([his.g_energyResVenergy_raw_gaussSigma for his in hsets], ['no corr.'])
dm.addHistos([his.g_energyResVenergy_raw_gaussSigma for his in hsets], ['no corr. NB'])

dm.addHistos([his.g_energyResVenergy_raw_effSigma for his in hsets], ['no corr. effSigma'])
dm.addHistos([his.g_energyResVenergy_raw_effSigma for his in hsets], ['no corr. effSigma NB'])

# dm.addHistos([his.g_energyResVenergy_lcalib_sigmaEOE for his in hsets], ['layer-calib.'])
# dm.addHistos([his.g_energyResVenergy_lcalib_effSigmaEOE for his in hsets], ['layercalib. effSigma'])

# # dm.addHistos([his.g_energyResVenergy_etacalib_sigmaEOE for his in hsets], ['eta+layer-calib.'])
# dm.addHistos([his.g_energyResVenergy_etacalib_effSigmaEOE for his in hsets], ['eta+layercalib. effSigma'])


dm.draw(text=text, options='COLZ', y_min=0., y_max=0.3)


In [102]:
dm = DrawMachine(rleg_config)
hsets, labels, text = hplot.get_histo(EnergyRes, 'ele-V9', 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaD', debug=False)

# dm.addHistos([his.g_energyResVenergy_raw_sigmaEOE for his in hsets], ['no corr.'])
dm.addHistos([his.g_energyResVenergy_raw_effSigma for his in hsets], ['no corr. effSigma'])

# dm.addHistos([his.g_energyResVenergy_lcalib_sigmaEOE for his in hsets], ['layer-calib.'])
dm.addHistos([his.g_energyResVenergy_lcalib_effSigma for his in hsets], ['layercalib. effSigma'])

# dm.addHistos([his.g_energyResVenergy_etacalib_sigmaEOE for his in hsets], ['eta+layer-calib.'])
dm.addHistos([his.g_energyResVenergy_etacalib_effSigma for his in hsets], ['eta+layercalib. effSigma'])


dm.draw(text=text, options='COLZ', y_min=0., y_max=0.3)


In [103]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaD', debug=False)
    hset_new = []
    labels_new = []

    hset_new.append(hsets[0].g_energyResVenergy_raw_gaussSigma)
    labels_new.append('no corr.')

    hset_new.append(hsets[0].g_energyResVenergy_lcalib_gaussSigma)
    labels_new.append('layer calib.')

    hset_new.append(hsets[0].g_energyResVenergy_etacalib_gaussSigma)
    labels_new.append('eta+ layer calib.')

    
    draw(hset_new, labels_new, options='L', text=text,  min_y=-0, max_y=0.1)


In [104]:
dm = DrawMachine(rleg_config)
hsets, labels, text = hplot.get_histo(EnergyRes, 'ele-V9', 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaBCD', debug=False)

# dm.addHistos([his.g_energyResVenergy_raw_sigmaEOE for his in hsets], ['no corr.'])
dm.addHistos([his.g_energyResVenergy_raw_effSigma for his in hsets], ['no corr. effSigma'])

# dm.addHistos([his.g_energyResVenergy_lcalib_sigmaEOE for his in hsets], ['layer-calib.'])
dm.addHistos([his.g_energyResVenergy_lcalib_effSigma for his in hsets], ['layercalib. effSigma'])

# dm.addHistos([his.g_energyResVenergy_etacalib_sigmaEOE for his in hsets], ['eta+layer-calib.'])
dm.addHistos([his.g_energyResVenergy_etacalib_effSigma for his in hsets], ['eta+layercalib. effSigma'])


dm.draw(text=text, options='COLZ', y_min=0., y_max=0.1)


In [106]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaBCD', debug=False)
    hset_new = []
    labels_new = []

    hset_new.append(hsets[0].g_energyResVenergy_raw_gaussSigma)
    labels_new.append('no corr.')

    hset_new.append(hsets[0].g_energyResVenergy_lcalib_gaussSigma)
    labels_new.append('layer calib.')

    hset_new.append(hsets[0].g_energyResVenergy_etacalib_gaussSigma)
    labels_new.append('eta+ layer calib.')

    
    draw(hset_new, labels_new, options='L', text=text,  min_y=-0, max_y=0.3)


In [108]:
for sample in ['ele-V9']:
    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDR'], ['Em'], 'GENEtaBC', debug=False)
    hset_new = []
    labels_new = []

    hset_new.append(hsets[0].g_energyResVenergy_raw_gaussSigma)
    labels_new.append('no int')

    hsets, labels, text = hplot.get_histo(EnergyRes, sample, 'PU200', ['HMvDRshapeDr'], ['Em'], 'GENEtaBC', debug=False)

    hset_new.append(hsets[0].g_energyResVenergy_raw_gaussSigma)
    labels_new.append('EM interp.')

    hset_new.append(hsets[0].g_energyResVenergy_etacalib_gaussSigma)
    labels_new.append('EM eta corr.')

#     hset_new.append(hsets[0].g_lCalibEnergyResVenergy_sigmaEOE)
#     labels_new.append('layer calib.')

#     hset_new.append(hsets[0].g_etalCalibEnergyResVenergy_sigmaEOE)
#     labels_new.append('eta+ layer calib.')

    
    draw(hset_new, labels_new, options='L', text=text,  min_y=-0, max_y=0.2)


## $p_{T}$ resolution

In [74]:
cache3 = pd.DataFrame(columns=['h_name', 'bin_limits', 'fit_function', 'results'])


In [86]:

for sample in ['photons-V9']:
    for tp in tps:
        for pu in ['PU0']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], 'GENEtaBC', debug=False)
    #         print dir(hsets[0])
            draw([his.h_ptResVpt_raw_graph('effSigmaEOE', '#sigma^{EFF}(p_{T})/p_{T}',  
                 lambda h2d: computeResolution(histo2d=h2d,
                                               bin_limits=[(7, 12), (13, 18), (19, 24), (25, 36),(37, 48), (49, 60), (61, 72), (73, 84), (85, 100)],
                                               y_axis_range=(-10, 10),
                                               fit_function=effective_sigma_energy,
                                               result_index=0,
                                               cache=cache2)) for his in hsets], labels, text=text, options='COLZ', min_y=0., max_y=0.1)
            


-----------------------
x_low: 6.0 x_high: 12.0
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_ptResVpt_raw, bin_limits: (7, 12), fit_function: <function effective_sigma_energy at 0x1372d6cf8>
x_low: 12.0 x_high: 18.0
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_ptResVpt_raw, bin_limits: (13, 18), fit_function: <function effective_sigma_energy at 0x1372d6cf8>
x_low: 18.0 x_high: 24.0
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_ptResVpt_raw, bin_limits: (19, 24), fit_function: <function effective_sigma_energy at 0x1372d6cf8>
x_low: 24.0 x_high: 36.0
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_ptResVpt_raw, bin_limits: (25, 36), fit_function: <function effective_sigma_energy at 0x1372d6cf8>
x_low: 36.0 x_high: 48.0
READ cached fit results h_name: photons-V9_PU0_HMvDR_Em_GENEtaBC_ptResVpt_raw, bin_limits: (37, 48), fit_function: <function effective_sigma_energy at 0x1372d6cf8>
x_low: 48.0 x_high: 60.0
READ cac

In [87]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot.get_histo(EnergyRes, 'photons-V9', 'PU0', ['HMvDR', 'HMvDRshapeDr'], ['Em'], 'GENEtaBC', debug=False)

dm.addHistos([his.g_ptResVpt_raw_effSigmaEOE for his in hsets], ['no int. (uncalib)', 'EM int (uncalib)'])
    
dm.draw(options='L', text=text,  y_min=-0, y_max=0.08)


In [226]:

for sample in ['ele-V9']:
    for tp in ['HMvDRshapeDr']:
        for pu in ['PU200']:
            hsets, labels, text = hplot.get_histo(EnergyRes, sample, pu, tp, ['Em'], ['GENEtaBC','GENEtaD'] , debug=False)
    #         print dir(hsets[0])
            draw([his.h_ptResVpt_raw_graph('effSigmaEOE', '#sigma^{EFF}(p_{T})/p_{T}',  
                 lambda h2d: computeResolution(histo2d=h2d,
                                               bin_limits=[(7, 12), (13, 18), (19, 24), (25, 36),(37, 48), (49, 60), (61, 72), (73, 84), (85, 100)],
                                               y_axis_range=(-10, 10),
                                               fit_function=effective_sigma_energy,
                                               result_index=0,
                                               cache=cache2)) for his in hsets], labels, text=text, options='COLZ', min_y=0., max_y=0.1)
            draw([his.h_ptResVpt_etacalib_graph('effSigmaEOE', '#sigma^{EFF}(p_{T})/p_{T}',  
                 lambda h2d: computeResolution(histo2d=h2d,
                                               bin_limits=[(7, 12), (13, 18), (19, 24), (25, 36),(37, 48), (49, 60), (61, 72), (73, 84), (85, 100)],
                                               y_axis_range=(-10, 10),
                                               fit_function=effective_sigma_energy,
                                               result_index=0,
                                               cache=cache2)) for his in hsets], labels, text=text, options='COLZ', min_y=0., max_y=0.1)
            


-----------------------
READ cached fit results h_name: ele-V9_PU200_HMvDRshapeDr_Em_GENEtaBC_ptResVpt_raw, bin_limits: (7, 12), fit_function: <function effective_sigma_energy at 0x25d254ed8>
READ cached fit results h_name: ele-V9_PU200_HMvDRshapeDr_Em_GENEtaBC_ptResVpt_raw, bin_limits: (13, 18), fit_function: <function effective_sigma_energy at 0x25d254ed8>
READ cached fit results h_name: ele-V9_PU200_HMvDRshapeDr_Em_GENEtaBC_ptResVpt_raw, bin_limits: (19, 24), fit_function: <function effective_sigma_energy at 0x25d254ed8>
READ cached fit results h_name: ele-V9_PU200_HMvDRshapeDr_Em_GENEtaBC_ptResVpt_raw, bin_limits: (25, 36), fit_function: <function effective_sigma_energy at 0x25d254ed8>
READ cached fit results h_name: ele-V9_PU200_HMvDRshapeDr_Em_GENEtaBC_ptResVpt_raw, bin_limits: (37, 48), fit_function: <function effective_sigma_energy at 0x25d254ed8>
READ cached fit results h_name: ele-V9_PU200_HMvDRshapeDr_Em_GENEtaBC_ptResVpt_raw, bin_limits: (49, 60), fit_function: <function ef

In [229]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot.get_histo(EnergyRes, 'ele-V9', 'PU200', ['HMvDRshapeDr'], ['Em'], ['GENEtaBC','GENEtaD'], debug=False)

dm.addHistos([his.g_ptResVpt_raw_effSigmaEOE for his in hsets], ['EM int (uncalib) etaBC', 'etaD'])
    
dm.draw(options='L', text=text,  y_min=-0, y_max=0.3)


In [230]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot.get_histo(EnergyRes, 'ele-V9', 'PU200', ['HMvDRshapeDr'], ['Em'], ['GENEtaBC','GENEtaD'], debug=False)

dm.addHistos([his.g_ptResVpt_etacalib_effSigmaEOE for his in hsets], ['EM int (uncalib) etaBC', 'etaD'])
    
dm.draw(options='L', text=text,  y_min=-0, y_max=0.3)
